<a href="https://colab.research.google.com/github/ArtemMusienko/ASR-with-Google-Web-Speech-API/blob/main/ASR_with_Google_Web_Speech_API.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Решение задачи:

Установим необходимый ряд библиотек:

In [ ]:
!pip install -q SpeechRecognition pydub jiwer ipywidgets kagglehub
!apt-get update && apt-get install -y ffmpeg > /dev/null 2>&1

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.9/32.9 MB 66.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 60.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 47.3 MB/s eta 0:00:00
Hit:1 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:2 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy-backports InRelease [127 kB]
Get:4 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Get:5 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,632 B]
Get:6 https://r2u.stat.illinois.edu/ubuntu jammy InRelease [6,555 B]
Get:7 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease [1,581 B]
Hit:8 https://cli.github.com/packages stable InRelease
Hit:9 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:10 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:11 https://ppa.l

Импортируем необходимые библиотеки:

In [ ]:
import os
import io
import numpy as np
import random
import json
import glob
from getpass import getpass

import warnings
# Игнорируем SyntaxWarning, которые появляются при импорте pydub
warnings.filterwarnings("ignore", category=SyntaxWarning, module='pydub')

from pydub import AudioSegment
import speech_recognition as sr
from jiwer import wer, cer
import pandas as pd
from IPython.display import Audio, display, HTML
from google.colab import files
import kagglehub

Выполним установку датасета через **Kaggle** и получим его путь расположения:

In [ ]:
print("Загрузка датасета с Kaggle...")
path = kagglehub.dataset_download("bryanpark/russian-single-speaker-speech-dataset")
print("Путь до файла: ", path)

Загрузка датасета с Kaggle...


100%|██████████| 6.16G/6.16G [01:04<00:00, 103MB/s]

Extracting files...


Путь до файла:  /root/.cache/kagglehub/datasets/bryanpark/russian-single-speaker-speech-dataset/versions/1


Этот блок задает константы `DATASET_PATH` и `TRANSCRIPT_FILE` для определения местоположения данных. Затем он использует библиотеку pandas для загрузки `transcript.txt`. С помощью `usecols=[0, 2]` и `names=['file_path', 'text']` он считывает только первую (путь к файлу) и третью (текст) колонки, игнорируя промежуточную, и сразу присваивает им правильные имена для дальнейшей работы.

In [ ]:
# Определяем финальный путь к данным
DATASET_PATH = "/root/.cache/kagglehub/datasets/bryanpark/russian-single-speaker-speech-dataset/versions/1"
TRANSCRIPT_FILE = os.path.join(DATASET_PATH, "transcript.txt")

# Загрузка транскриптов
try:
    df = pd.read_csv(
        TRANSCRIPT_FILE,
        sep='|',
        header=None,
        usecols=[0, 2],  # Используем колонку 0 (ПУТЬ) и 2 (ТЕКСТ)
        names=['file_path', 'text']  # Называем колонку 0 'file_path', а колонку 2 'text'
    )

    print(f"Загружено {len(df)} записей: ")
    display(df.head())
except Exception as e:
    print(f"Ошибка при чтении transcript.txt: {e}")
    print("Убедись, что файл находится по правильному пути!")

Загружено 9599 записей: 


file_path  \
0  early_short_stories/early_short_stories_0001.wav   
1  early_short_stories/early_short_stories_0002.wav   
2  early_short_stories/early_short_stories_0003.wav   
3  early_short_stories/early_short_stories_0004.wav   
4  early_short_stories/early_short_stories_0005.wav   

                                                text  
0  За столицей мудрого царя Соломона шелестел по ...  
1  где происходили свидания Ариэля и Тамары. Ему ...  
2  Но Ариэль был сыном знатного иерусалимца, одно...  
3  и его волосы были черны, как ночь, а глаза — к...  
4  не дозволялось обитать среди иудеев, и ее мягк...

Этот блок определяет две ключевые функции. `recognize_audio` — это функция-обертка для **SpeechRecognition**, которая принимает путь к файлу (или буфер), считывает аудио и отправляет его в **Google Web Speech API**, возвращая распознанный текст. `create_noisy_audio` — более сложная функция: она загружает аудиофайл с помощью pydub, генерирует "белый шум" (массив случайных чисел numpy) той же длительности, накладывает этот шум поверх чистого аудио и экспортирует зашумленный результат в буфер памяти в формате **WAV**:

In [ ]:
def recognize_audio(audio_file_path_or_buffer):
    """
    Распознавание речи с использованием Google Web Speech API.
    """
    recognizer = sr.Recognizer()
    recognizer.energy_threshold = 300
    recognizer.dynamic_energy_threshold = True
    recognizer.pause_threshold = 0.8

    try:
        with sr.AudioFile(audio_file_path_or_buffer) as source:
            recognizer.adjust_for_ambient_noise(source, duration=0.2)
            audio = recognizer.record(source)

        text = recognizer.recognize_google(audio, language="ru-RU")
        return text
    except sr.UnknownValueError:
        return "<не удалось распознать речь>"
    except sr.RequestError as e:
        return f"<ошибка сервиса: {e}>"

def create_noisy_audio(file_path, noise_level_db=-15):
    """
    Добавление белого шума к аудиофайлу.
    """
    try:
        # Загружаем чистый звук (читает любой формат)
        clean_audio = AudioSegment.from_file(file_path)

        num_samples = clean_audio.frame_count()

        # Резервный вариант, если frame_count() не сработал
        if not num_samples:
             duration_ms = len(clean_audio)
             num_samples = int(duration_ms * clean_audio.frame_rate / 1000)

        # Гарантируем, что num_samples - это integer, а не float
        num_samples = int(num_samples)

        # Генерируем сэмплы шума
        if clean_audio.channels == 2:
            noise_data = np.random.randint(-32768, 32767, size=(num_samples, 2)).astype(np.int16)
        else:
            noise_data = np.random.randint(-32768, 32767, size=num_samples).astype(np.int16)

        # Создаем AudioSegment из шума
        noise = AudioSegment(
            noise_data.tobytes(),
            frame_rate=clean_audio.frame_rate,
            sample_width=clean_audio.sample_width,
            channels=clean_audio.channels
        )

        # Применяем усиление к шуму
        noise = noise + noise_level_db
        noisy_audio = clean_audio.overlay(noise, loop=True)

        # Экспортируем результат в буфер в памяти
        wav_io = io.BytesIO()
        noisy_audio.export(wav_io, format='wav')
        wav_io.seek(0)

        # Возвращаем буфер (для `sr` и `Audio`) и объект (для `display`)
        return wav_io, noisy_audio

    except Exception as e:
        print(f"Ошибка при добавлении шума: {e}")
        return None, None

Это главный блок эксперимента. Он выбирает 5 случайных аудиофайлов и запускает цикл. Внутри цикла для каждого файла он:
1) принудительно конвертирует оригинальный файл в чистый **WAV-буфер**;
2) распознает этот чистый буфер и считает метрики **WER/CER**;
3) вызывает `create_noisy_audio` для создания зашумленной версии;
4) распознает зашумленный буфер и считает его **WER/CER**;
5) отображает оба аудиофайла (чистый и с шумом) для прослушивания, и сохраняет все результаты в список `results`.

In [ ]:
# Выбираем 5 случайных образцов для теста
N_EXAMPLES = 5
if len(df) >= N_EXAMPLES:
    samples = df.sample(N_EXAMPLES)
else:
    print(f"В датасете меньше {N_EXAMPLES} примеров, используем все.")
    samples = df

results = []

print(f"Начинаем обработку {N_EXAMPLES} случайных аудиофайлов...\n")
print("="*70)

for index, row in samples.iterrows():
    file_path = os.path.join(DATASET_PATH, row['file_path'])
    original_text = row['text'].lower()

    print(f"--- Обработка файла: {row['file_path']} ---")
    print(f"Оригинал (текст): {original_text}")

    # Конвертация в чистый WAV
    try:
        clean_segment = AudioSegment.from_file(file_path)
        clean_wav_buffer = io.BytesIO()
        clean_segment.export(clean_wav_buffer, format='wav')
        clean_wav_buffer.seek(0)
    except Exception as e:
        print(f"Ошибка чтения/конвертации {file_path}: {e}. Пропускаем файл.\n")
        print("="*70 + "\n")
        continue

    # Распознавание чистого аудио
    print("\nРаспознавание чистого аудио...")
    text_clean = recognize_audio(clean_wav_buffer).lower()

    # Расчет метрик (WER и CER)
    wer_clean = wer(original_text, text_clean)
    cer_clean = cer(original_text, text_clean)

    print(f"Результат (чистый): {text_clean}")
    print(f"WER (чистый): {wer_clean:.2%}")
    print(f"CER (чистый): {cer_clean:.2%}")

    # Создание и распознавание зашумленного аудио
    print("\nДобавление шума и распознавание...")
    noisy_wav_buffer, noisy_audio_obj = create_noisy_audio(file_path, noise_level_db=-30)

    text_noisy = "<ошибка создания шума>"
    wer_noisy = 1.0
    cer_noisy = 1.0

    if noisy_wav_buffer:
        text_noisy = recognize_audio(noisy_wav_buffer).lower()
        wer_noisy = wer(original_text, text_noisy)
        cer_noisy = cer(original_text, text_noisy)

    print(f"Результат (с шумом): {text_noisy}")
    print(f"WER (с шумом): {wer_noisy:.2%}")
    print(f"CER (с шумом): {cer_noisy:.2%}")

    # Вывод аудио
    print("\n--- Прослушивание аудио ---")
    print("Чистый (Оригинал):")
    display(Audio(file_path))

    if noisy_wav_buffer: # Проверяем, что буфер создался
        print("С шумом:")
        # Используем .getvalue() для получения полного WAV-файла из буфера
        display(Audio(noisy_wav_buffer.getvalue()))

    # Сохраняем расширенные результаты
    results.append({
        "Файл": row['file_path'],
        "Оригинал": original_text,
        "Распознано (чистый)": text_clean,
        "WER (чистый)": wer_clean,
        "CER (чистый)": cer_clean,
        "Распознано (с шумом)": text_noisy,
        "WER (с шумом)": wer_noisy,
        "CER (с шумом)": cer_noisy
    })

    print("\n" + "="*70 + "\n")

print("--- Эксперимент завершен ---")

Начинаем обработку 5 случайных аудиофайлов...

--- Обработка файла: early_short_stories/early_short_stories_0654.wav ---
Оригинал (текст): увидев большой пакет, который принес с собою муж, она радостно спросила: — нашлась?

Распознавание чистого аудио...
Результат (чистый): увидев большой пакет который принёс с собой муж она радостно спросила нашлась
WER (чистый): 53.85%
CER (чистый): 9.64%

Добавление шума и распознавание...
Результат (с шумом): увидев большой пакет который принёс с собой муж она радость и спросила пришла
WER (с шумом): 61.54%
CER (с шумом): 18.07%

--- Прослушивание аудио ---
Чистый (Оригинал):


С шумом:




--- Обработка файла: shortstories_childrenadults/shortstories_childrenadults_3059.wav ---
Оригинал (текст): — не в состоянии удержать его жить, потому что выдохлись . да и не выдохлись,

Распознавание чистого аудио...
Результат (чистый): не в состоянии удержать его жить потому что выдохлись да и не выдохлись
WER (чистый): 26.67%
CER (чистый): 7.79%

Добавление шума и распознавание...
Результат (с шумом): не в состоянии удержать его жизнь потому что выдохлись да и не выдохлись
WER (с шумом): 26.67%
CER (с шумом): 10.39%

--- Прослушивание аудио ---
Чистый (Оригинал):


С шумом:




--- Обработка файла: early_short_stories/early_short_stories_1567.wav ---
Оригинал (текст): и нет-нет — из этой кучки выделится знакомая фигура, подойдет и выскажет мнение.

Распознавание чистого аудио...
Результат (чистый): нет нет из этой кучки выделяться знакомая фигура подойдёт и выскажет мнение
WER (чистый): 53.85%
CER (чистый): 12.50%

Добавление шума и распознавание...
Результат (с шумом): из этой кучки выделится знакомая фигура подойдёт и выскажет мнение
WER (с шумом): 46.15%
CER (с шумом): 18.75%

--- Прослушивание аудио ---
Чистый (Оригинал):


...



--- Обработка файла: shortstories_childrenadults/shortstories_childrenadults_0707.wav ---
Оригинал (текст): кое-где гайки попробует подвинтить, щебёнку подровняет, водяные трубы посмотрит

Распознавание чистого аудио...
Результат (чистый): ой где гайки попробуют подвиг щебёнка подровняли водяные трубы посмотрит
WER (чистый): 66.67%
CER (чистый): 17.72%

Добавление шума и распознавание...
Результат (с шумом): ой где гайки попробуют подвиг щебёнка подровняли водяные трубы посмотрит
WER (с шумом): 66.67%
CER (с шумом): 17.72%

--- Прослушивание аудио ---
Чистый (Оригинал):


С шумом:




--- Обработка файла: shortstories_childrenadults/shortstories_childrenadults_2717.wav ---
Оригинал (текст): когда начальство заметило, что наказание, налагаемое им на никиту, не только не причиняет ему огорчения, а даже доставляет радость,

Распознавание чистого аудио...
Результат (чистый): когда начальство заметила что наказание налагаемое им на никиту не только не причиняет ему огорчения а даже доставляет радость
WER (чистый): 26.32%
CER (чистый): 4.58%

Добавление шума и распознавание...
Результат (с шумом): когда начальство заметила что наказание налагаемое им на никиту не только не причиняет ему огорчения а даже доставляет радость
WER (с шумом): 26.32%
CER (с шумом): 4.58%

--- Прослушивание аудио ---
Чистый (Оригинал):


С шумом:




--- Эксперимент завершен ---


Этот финальный блок кода собирает все данные, накопленные в списке `results`, и преобразует их в** pandas DataFrame** для удобного отображения. Он применяет форматирование к колонкам с метриками, чтобы они отображались в виде процентов (например, 25.50% вместо 0.255). Наконец, он выводит на экран **HTML-таблицу** с итоговыми результатами:

In [ ]:
# Представление итоговых результатов
results_df = pd.DataFrame(results)
display(HTML("<h3>Итоговые результаты распознавания (WER / CER)</h3>"))

# Форматируем колонки для лучшего отображения
results_df['WER (чистый)'] = results_df['WER (чистый)'].map('{:.2%}'.format)
results_df['CER (чистый)'] = results_df['CER (чистый)'].map('{:.2%}'.format)
results_df['WER (с шумом)'] = results_df['WER (с шумом)'].map('{:.2%}'.format)
results_df['CER (с шумом)'] = results_df['CER (с шумом)'].map('{:.2%}'.format)

display(results_df)

Файл  \
0   early_short_stories/early_short_stories_0654.wav   
1  shortstories_childrenadults/shortstories_child...   
2   early_short_stories/early_short_stories_1567.wav   
3  shortstories_childrenadults/shortstories_child...   
4  shortstories_childrenadults/shortstories_child...   

                                            Оригинал  \
0  увидев большой пакет, который принес с собою м...   
1  — не в состоянии удержать его жить, потому что...   
2  и нет-нет — из этой кучки выделится знакомая ф...   
3  кое-где гайки попробует подвинтить, щебёнку по...   
4  когда начальство заметило, что наказание, нала...   

                                 Распознано (чистый) WER (чистый)  \
0  увидев большой пакет который принёс с собой му...       53.85%   
1  не в состоянии удержать его жить потому что вы...       26.67%   
2  нет нет из этой кучки выделяться знакомая фигу...       53.85%   
3  ой где гайки попробуют подвиг щебёнка подровня...       66.67%   
4  когда начальство заметила что наказание налага...       26.32%   

  CER (чистый)                               Распознано (с шумом)  \
0        9.64%  увидев большой пакет который принёс с собой му...   
1        7.79%  не в состоянии удержать его жизнь потому что в...   
2       12.50%  из этой кучки выделится знакомая фигура подойд...   
3       17.72%  ой где гайки попробуют подвиг щебёнка подровня...   
4        4.58%  когда начальство заметила что наказание налага...   

  WER (с шумом) CER (с шумом)  
0        61.54%        18.07%  
1        26.67%        10.39%  
2        46.15%        18.75%  
3        66.67%        17.72%  
4        26.32%         4.58%

## Вывод:

Для оценки качества нашей **ASR-системы** мы использовали две ключевые метрики: **WER (Word Error Rate)** и **CER (Character Error Rate)**:
* **WER (Word Error Rate)** Почему выбрана: Это золотой стандарт в индустрии **ASR**. Она измеряет долю неверно распознанных слов (учитывая замены, вставки и удаления) и отлично показывает, насколько хорошо система поняла общий смысл сказанного;
* **CER (Character Error Rate)** Почему выбрана: **CER** измеряет долю неверно распознанных символов. Мы добавили эту метрику, так как она критически важна для русского языка. Русский язык — флективный, и изменение одного-двух символов (окончания) может полностью изменить падеж, число или даже смысл слова (например, "дом" -> "дома"). **WER** посчитает это одной ошибкой ("Замена"), но CER покажет, насколько серьезной была эта ошибка на символьном уровне.



В результате выполнения кода можно отметить неплохие результаты. Системных ошибок не обнаружено. Белый шум подобран корректно, и был достигнут оптимальный баланс для его внедрения в речь. Это позволило модели успешно распознать речь как в оригинальном виде, так и с добавлением шума.